# Battle of the Neighborhoods
## New York City vs Portland OR

This notebook compares neighborhoods between New York City and Portland OR using Foursquare data to determine which neighborhoods are similar between the two cities.  A dashboard provides the user with the ability to select which city they are moving to and what neighborhood they currently live in.  The dashboard will display a folio map of the comparable neighborhoods in the destination city and will list the neighborhoods in a table along with their top 10 venue types.

Load all the libraries we will need for analysis

In [ ]:
!pip uninstall -y numpy
!pip install numpy
!pip install dash
!pip install jupyter-dash

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

#import libraries for dashboard
import dash
import dash_html_components as html
import dash_core_components as dcc
from dash.dependencies import Input, Output
from jupyter_dash import JupyterDash
import dash_table


print('Libraries imported.')


Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


Go get the New York City neighborhood information and process it into a data frame

In [2]:
# get the NYC file
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')

# read the file
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

#assign data
neighborhoods_data = newyork_data['features']

# create a list with the two city names in it
cities = ['New York City', 'Portland']

#process the file into dataframe
# define the dataframe columns
column_names = ['City', 'Area', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

# cycle through neighborhoods data and assign to dataframe
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'City': cities[0],
                                          'Area': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)


Data downloaded!


Now load the Portland neighborhood data and append it to the neighborhoods dataframe

In [3]:

import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.
client_9a4900c51b86461e8e56e332fd174846 = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='removed for security',
    ibm_auth_endpoint="https://iam.cloud.ibm.com/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_9a4900c51b86461e8e56e332fd174846.get_object(Bucket='capstoneproject-donotdelete-pr-g6gysetnvfvfbo',Key='Neighborhoods_Portland.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

portland_data = pd.read_csv(body)


In [4]:
portland_data.head()

City  Area Neighborhood  Latitude  Longitude
0  Portland  East        ARGAY   45.5545  -122.5213
1  Portland  East   CENTENNIAL   45.5046  -122.4967
2  Portland  East     GLENFAIR   45.5235  -122.5049
3  Portland  East    HAZELWOOD   45.5264  -122.5377
4  Portland  East    HAZELWOOD   45.5264  -122.5377

Add the Portland data to the NYC data

In [5]:
#append the Portland data to the neighborhoods dataframe
neighborhoods=neighborhoods.append(portland_data, ignore_index = True)


In [6]:
neighborhoods.head()

City   Area Neighborhood   Latitude  Longitude
0  New York City  Bronx    Wakefield  40.894705 -73.847201
1  New York City  Bronx   Co-op City  40.874294 -73.829939
2  New York City  Bronx  Eastchester  40.887556 -73.827806
3  New York City  Bronx    Fieldston  40.895437 -73.905643
4  New York City  Bronx    Riverdale  40.890834 -73.912585

Now from the neighborhoods dataframe create a couple of lists comprising the neighborhoods for each city

In [7]:
#NYC neighborhoods
NYC_Neighborhoods = neighborhoods.query('City=="New York City"')['Neighborhood'].tolist()
NYC_Neighborhoods.sort()
NYC_Neighborhoods
#Portland neighborhoods
Portland_Neighborhoods = neighborhoods.query('City=="Portland"')['Neighborhood'].tolist()
Portland_Neighborhoods.sort()
Portland_Neighborhoods

#Get lat/long for NYC
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
NYC_latitude = location.latitude
NYC_longitude = location.longitude

#Get lat/long for Portland
address = 'Portland, OR'

geolocator = Nominatim(user_agent="pt_explorer")
location = geolocator.geocode(address)
Portland_latitude = location.latitude
Portland_longitude = location.longitude

print('NYC lat/long: are {}, {}.'.format(NYC_latitude, NYC_longitude))
print('Portland lat/long: are {}, {}.'.format(Portland_latitude, Portland_longitude))

NYC lat/long: are 40.7127281, -74.0060152.
Portland lat/long: are 45.5202471, -122.6741949.


Establish constants for Foursquare calls

In [19]:
#Foursquare credentials
CLIENT_ID = 'removed for security' # your Foursquare ID
CLIENT_SECRET = 'removed for security' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value


Define a function to return venue data for a location

In [9]:
#function to return nearby venues for a particular location
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        #some requests are coming back empty so check to make sure we got results
        if results:
            
            #return only relevant information for each nearby venue
            venues_list.append([(
            name,
            lat,
            lng,
            v['venue']['name'],
            v['venue']['location']['lat'],
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']) for v in results])
            
        else:
            print("no results for: ", name)
            
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                             'Neighborhood Latitude', 
                             'Neighborhood Longitude', 
                             'Venue', 
                             'Venue Latitude', 
                             'Venue Longitude', 
                             'Venue Category']
    
    return(nearby_venues)

Go get all the venue information for both cities

In [10]:
#get all venues
all_venues=getNearbyVenues(neighborhoods['Neighborhood'], neighborhoods['Latitude'], neighborhoods['Longitude'])

print("Shape: ", all_venues.shape)
all_venues.head()

all_venues.groupby('Neighborhood').count

print('There are {} uniques categories.'.format(len(all_venues['Venue Category'].unique())))

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

Analyze each neighborhood and create a dataframe showing the different venue categories for each

In [11]:
# one hot encoding
all_onehot = pd.get_dummies(all_venues[['Venue Category']], prefix="", prefix_sep="")

#one of the venue categories is called neighborhood so go ahead and drop that one
all_onehot.drop(['Neighborhood'], axis=1, inplace=True)

# add neighborhood column back to dataframe on the first column
all_onehot.insert(0, "Neighborhood", all_venues['Neighborhood'], True) 

all_onehot.head()

Neighborhood  ATM  Accessories Store  Adult Boutique  Afghan Restaurant  \
0    Wakefield    0                  0               0                  0   
1    Wakefield    0                  0               0                  0   
2    Wakefield    0                  0               0                  0   
3    Wakefield    0                  0               0                  0   
4    Wakefield    0                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Amphitheater  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0       0                 0                       0   
1             0       0                 0                       0   
2             0       0                 0                       0   
3             0       0                 0                       0   
4             0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Assisted Living  Athletics & Sports  Auditorium  \
0                 0                0                   0           0   
1                 0                0                   0           0   
2                 0                0                   0           0   
3                 0                0                   0           0   
4                 0                0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Garage  Auto Workshop  \
0                      0                    0            0              0   
1                      0                    0            0              0   
2                      0                    0            0              0   
3                      0                    0            0              0   
4                      0                    0            0              0   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                0          0           0           0       0     0    0   
1                0          0           0           0       0     0    0   
2                0          0           0           0       0     0    0   
3                0          0           0           0       0     0    0   
4                0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Bath House  Beach  \
0               0                 0                 0           0      0   
1               0                 0                 0           0      0   
2               0                 0                 0           0      0   
3               0                 0                 0           0      0   
4               0                 0                 0           0      0   

   Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0          0                0         0            0           0   
1          0                0         0            0           0   
2          0                0         0            0           0   
3          0                0         0            0           0   
4          0                0         0            0           0  

Now groupby neighborhoods and generate the mean for each category to be used in the K-means

In [12]:
#create new df with mean of categories by neighborhood
all_grouped = all_onehot.groupby('Neighborhood').mean().reset_index()

print("Shape: ", all_grouped.shape)
all_grouped

Shape:  (390, 456)


Neighborhood       ATM  Accessories Store  Adult Boutique  \
0                      ALAMEDA  0.000000           0.000000        0.000000   
1                  ARBOR LODGE  0.000000           0.000000        0.000000   
2                    ARDENWALD  0.000000           0.000000        0.000000   
3                        ARGAY  0.000000           0.000000        0.000000   
4            ARLINGTON HEIGHTS  0.000000           0.000000        0.000000   
5                     Allerton  0.000000           0.000000        0.000000   
6                     Annadale  0.000000           0.000000        0.000000   
7                Arden Heights  0.000000           0.000000        0.000000   
8                    Arlington  0.000000           0.000000        0.000000   
9                     Arrochar  0.000000           0.000000        0.000000   
10                     Arverne  0.000000           0.000000        0.000000   
11                     Astoria  0.000000           0.000000        0.000000   
12             Astoria Heights  0.000000           0.000000        0.000000   
13                  Auburndale  0.000000           0.000000        0.000000   
14           BEAUMONT-WILSHIRE  0.000000           0.000000        0.000000   
15                       BOISE  0.000000           0.000000        0.000000   
16        BRENTWOOD-DARLINGTON  0.000000           0.000000        0.000000   
17                   BRIDGETON  0.000000           0.000000        0.000000   
18                  BRIDLEMILE  0.000000           0.000000        0.000000   
19                    BROOKLYN  0.000000           0.000000        0.000000   
20                     BUCKMAN  0.000000           0.000000        0.000000   
21                  Bath Beach  0.000000           0.023256        0.000000   
22           Battery Park City  0.000000           0.000000        0.000000   
23                   Bay Ridge  0.000000           0.000000        0.000000   
24                 Bay Terrace  0.000000           0.021277        0.000000   
25                  Baychester  0.000000           0.000000        0.000000   
26                     Bayside  0.000000           0.000000        0.000000   
27                   Bayswater  0.000000           0.000000        0.000000   
28                Bedford Park  0.000000           0.000000        0.000000   
29          Bedford Stuyvesant  0.000000           0.000000        0.000000   
30                  Beechhurst  0.000000           0.000000        0.000000   
31                    Bellaire  0.000000           0.000000        0.000000   
32                Belle Harbor  0.000000           0.000000        0.000000   
33                   Bellerose  0.000000           0.000000        0.000000   
34                     Belmont  0.000000           0.000000        0.000000   
35                 Bensonhurst  0.000000           0.000000        0.000000   
36                Bergen Beach  0.000000           0.000000        0.000000   
37                  Blissville  0.000000           0.000000        0.000000   
38                  Bloomfield  0.000000           0.000000        0.000000   
39                 Boerum Hill  0.000000           0.000000        0.000000   
40                Borough Park  0.000000           0.000000        0.000000   
41                Breezy Point  0.000000           0.000000        0.000000   
42                   Briarwood  0.000000           0.000000        0.000000   
43              Brighton Beach  0.000000           0.000000        0.000000   
44               Broad Channel  0.000000           0.000000        0.000000   
45           Broadway Junction  0.000000           0.000000        0.000000   
46                   Bronxdale  0.000000           0.000000        0.000000   
47            Brooklyn Heights  0.000000           0.000000        0.000000   
48                  Brookville  0.000000           0.000000        0.000000   
49                 Brownsville  0.000000           0.000000        0

In [13]:
#function to sort venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]


Generate a dataframe containing the top 10 venues in each neighborhood

In [71]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = all_grouped['Neighborhood']

for ind in np.arange(all_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(all_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0            ALAMEDA             Pet Store    Italian Restaurant   
1        ARBOR LODGE     Convenience Store    Mexican Restaurant   
2          ARDENWALD           Coffee Shop                  Café   
3              ARGAY                   Bar          Intersection   
4  ARLINGTON HEIGHTS                Garden           Bus Station   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0          Optical Shop         Garden Center          Soccer Field   
1            Playground           Video Store                   Gym   
2         Grocery Store                   ATM          Outlet Store   
3     Convenience Store            Playground       Thai Restaurant   
4                  Café      Botanical Garden             Gift Shop   

  6th Most Common Venue  7th Most Common Venue  8th Most Common Venue  \
0              Bus Stop            Coffee Shop  Performing Arts Venue   
1           Pizza Place                   Park        Thai Restaurant   
2           Pet Service               Pet Café    Peruvian Restaurant   
3     Paella Restaurant              Pet Store            Pet Service   
4          Tennis Court  Performing Arts Venue       Pedestrian Plaza   

           9th Most Common Venue 10th Most Common Venue  
0  Paper / Office Supplies Store                   Park  
1           Marijuana Dispensary            Coffee Shop  
2             Persian Restaurant  Performing Arts Venue  
3                       Pet Café    Peruvian Restaurant  
4                    Outlet Mall     Persian Restaurant

Now run K-means to cluster neighborhoods into 7 different clusters

In [72]:
# set number of clusters
kclusters = 6

all_grouped_clustering = all_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(all_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 4, 4, 4, 4, 2, 3, 3, 0, 3], dtype=int32)

Now create a new dataframe merging cluster information with top venue information for each neighborhood

In [73]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster_Labels', kmeans.labels_)

neighborhoods_merged = neighborhoods

# merge venue data with neighborhood data to add latitude/longitude for each neighborhood
neighborhoods_merged = neighborhoods_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood', how='right')

#drop the latitude and longitude columns
neighborhoods_merged.drop(['Latitude'], axis=1, inplace=True)
neighborhoods_merged.drop(['Longitude'], axis=1, inplace=True)

neighborhoods_merged.head() 

City       Area       Neighborhood  Cluster_Labels  \
331  Portland  Northeast            ALAMEDA               0   
320  Portland      North        ARBOR LODGE               4   
362  Portland  Southeast          ARDENWALD               4   
306  Portland       East              ARGAY               4   
352  Portland  Northwest  ARLINGTON HEIGHTS               4   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
331             Pet Store    Italian Restaurant          Optical Shop   
320     Convenience Store    Mexican Restaurant            Playground   
362           Coffee Shop                  Café         Grocery Store   
306                   Bar          Intersection     Convenience Store   
352                Garden           Bus Station                  Café   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
331         Garden Center          Soccer Field              Bus Stop   
320           Video Store                   Gym           Pizza Place   
362                   ATM          Outlet Store           Pet Service   
306            Playground       Thai Restaurant     Paella Restaurant   
352      Botanical Garden             Gift Shop          Tennis Court   

     7th Most Common Venue  8th Most Common Venue  \
331            Coffee Shop  Performing Arts Venue   
320                   Park        Thai Restaurant   
362               Pet Café    Peruvian Restaurant   
306              Pet Store            Pet Service   
352  Performing Arts Venue       Pedestrian Plaza   

             9th Most Common Venue 10th Most Common Venue  
331  Paper / Office Supplies Store                   Park  
320           Marijuana Dispensary            Coffee Shop  
362             Persian Restaurant  Performing Arts Venue  
306                       Pet Café    Peruvian Restaurant  
352                    Outlet Mall     Persian Restaurant

Output the results of all the clusters

In [74]:
#Cluster 1
neighborhoods_merged.loc[neighborhoods_merged['Cluster_Labels'] == 0, :]

City           Area      Neighborhood  Cluster_Labels  \
331       Portland      Northeast           ALAMEDA               0   
227  New York City  Staten Island         Arlington               0   
245  New York City  Staten Island        Bloomfield               0   
172  New York City         Queens      Breezy Point               0   
238  New York City  Staten Island      Butler Manor               0   
258  New York City  Staten Island          Elm Park               0   
305  New York City  Staten Island         Fox Hills               0   
371       Portland      Southeast       LAURELHURST               0   
77   New York City       Brooklyn   Manhattan Beach               0   
206  New York City  Staten Island  Mariner's Harbor               0   
198  New York City  Staten Island      New Brighton               0   
224  New York City  Staten Island         Park Hill               0   
205  New York City  Staten Island     Port Richmond               0   
346       Portland      Northeast             SABIN               0   
286  New York City  Staten Island      Sandy Ground               0   
204  New York City  Staten Island       South Beach               0   
217  New York City  Staten Island       Tottenville               0   
318       Portland           East            WILKES               0   
285  New York City  Staten Island       Willowbrook               0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
331             Pet Store    Italian Restaurant          Optical Shop   
227              Bus Stop         Deli / Bodega   American Restaurant   
245     Recreation Center          Burger Joint              Bus Stop   
172                 Beach   Monument / Landmark              Bus Stop   
238        Baseball Field                  Pool           Gas Station   
258         Deli / Bodega              Bus Stop    Chinese Restaurant   
305              Bus Stop        Sandwich Place         Grocery Store   
371              Bus Stop           Bus Station      Asian Restaurant   
77               Bus Stop           Pizza Place            Playground   
206         Deli / Bodega    Italian Restaurant              Bus Stop   
198         Deli / Bodega                  Park              Bus Stop   
224              Bus Stop    Athletics & Sports           Coffee Shop   
205              Bus Stop            Donut Shop            Food Truck   
346              Bus Stop                   Bar  Marijuana Dispensary   
286              Bus Stop          Intersection             Racetrack   
204                  Pier         Deli / Bodega                 Beach   
217              Bus Stop         Deli / Bodega    Mexican Restaurant   
318        Sandwich Place     Convenience Store                   Bar   
285              Bus Stop         Deli / Bodega    Chinese Restaurant   

    4th Most Common Venue       5th Most Common Venue 6th Most Common Venue  \
331         Garden Center                Soccer Field              Bus Stop   
227           Coffee Shop                         ATM  Pakistani Restaurant   
245            Theme Park                         ATM           Outlet Mall   
172                 Trail                         ATM           Pet Service   
238              Bus Stop                 Outlet Mall           Pet Service   
258            Toll Plaza          Italian Restaurant   American Restaurant   
305           Outlet Mall                 Pet Service              Pet Café   
371     Elementary School            Sculpture Garden                   ATM   
77                  Beach              Sandwich Place        Ice Cream Shop   
206    Athletics & Sports                 Supermarket      Pedestrian Plaza   
198        Discount Store               Bowling Alley               Daycare   
224                 Hotel        Gym / Fitness Center                   ATM   
205           Pizza Place  Construction & Landscaping   Martial Arts School   
346      Sushi Restaurant 

In [75]:
#Cluster 2
neighborhoods_merged.loc[neighborhoods_merged['Cluster_Labels'] == 1, :]

City       Area          Neighborhood  Cluster_Labels  \
363       Portland  Southeast  BRENTWOOD-DARLINGTON               1   
384       Portland  Southwest            BRIDLEMILE               1   
91   New York City   Brooklyn          Bergen Beach               1   
385       Portland  Southwest          COLLINS VIEW               1   
27   New York City      Bronx          Clason Point               1   
308       Portland       East              GLENFAIR               1   
389       Portland  Southwest         HEALY HEIGHTS               1   
354       Portland  Northwest              HILLSIDE               1   
392       Portland  Southwest             MAPLEWOOD               1   
314       Portland       East      PARKROSE HEIGHTS               1   
317       Portland       East               RUSSELL               1   
4    New York City      Bronx             Riverdale               1   
148  New York City     Queens      South Ozone Park               1   

          1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
363                     Dog Run         Deli / Bodega                  Park   
384                        Park          Tennis Court                   ATM   
91              Harbor / Marina                  Park          Hockey Field   
385                        Park                 Hotel                Lawyer   
27                         Park                  Pool         Grocery Store   
308  Construction & Landscaping          Home Service                  Park   
389                    Bus Line                  Park                   ATM   
354                       Trail                  Park        Scenic Lookout   
392              Baseball Field           Coffee Shop                  Park   
314         American Restaurant              Bus Stop                  Park   
317                Optical Shop                  Park                   ATM   
4                   Bus Station                  Park                  Bank   
148                        Park         Deli / Bodega            Food Truck   

    4th Most Common Venue      5th Most Common Venue 6th Most Common Venue  \
363                   ATM                  Pet Store           Pet Service   
384           Outlet Mall                Pet Service              Pet Café   
91             Playground         Athletics & Sports        Baseball Field   
385                   ATM               Outlet Store             Pet Store   
27          Boat or Ferry  South American Restaurant              Bus Stop   
308                   ATM               Outlet Store             Pet Store   
389           Outlet Mall                Pet Service              Pet Café   
354           Music Venue                     Museum                   ATM   
392     Paella Restaurant                   Pharmacy             Pet Store   
314               Theater                        ATM          Outlet Store   
317          Outlet Store                  Pet Store           Pet Service   
4                   Plaza                        Gym          Outlet Store   
148  Fast Food Restaurant             Sandwich Place                  Food   

    7th Most Common Venue 8th Most Common Venue  9th Most Common Venue  \
363              Pet Café   Peruvian Restaurant     Persian Restaurant   
384   Peruvian Restaurant    Persian Restaurant  Performing Arts Venue   
91                    ATM  Pakistani Restaurant              Pet Store   
385           Pet Service              Pet Café    Peruvian Restaurant   
27      Convenience Store     Paella Restaurant   Pakistani Restaurant   
308           Pet Service              Pet Café    Peruvian Restaurant   
389   Peruvian Restaurant    Persian Restaurant  Performing Arts Venue   
354           Pet Service              Pet Café    Peruvian Restaurant   
392           Pet Service              Pet Café    Peruvian Restaurant   
314           Pet Service              Pet Café    Peruvian Restaurant   
317  

In [76]:
#Cluster 3
neighborhoods_merged.loc[neighborhoods_merged['Cluster_Labels'] == 2, :]

City           Area         Neighborhood  Cluster_Labels  \
298  New York City          Bronx             Allerton               2   
266  New York City         Queens      Astoria Heights               2   
10   New York City          Bronx           Baychester               2   
174  New York City         Queens           Beechhurst               2   
194  New York City         Queens             Bellaire               2   
278  New York City         Queens           Blissville               2   
159  New York City         Queens            Briarwood               2   
171  New York City         Queens        Broad Channel               2   
282  New York City       Brooklyn    Broadway Junction               2   
193  New York City         Queens           Brookville               2   
60   New York City       Brooklyn          Brownsville               2   
168  New York City         Queens      Cambria Heights               2   
74   New York City       Brooklyn             Canarsie               2   
267  New York City          Bronx    Claremont Village               2   
253  New York City  Staten Island              Clifton               2   
1    New York City          Bronx           Co-op City               2   
149  New York City         Queens        College Point               2   
43   New York City          Bronx            Concourse               2   
268  New York City          Bronx    Concourse Village               2   
71   New York City       Brooklyn        Cypress Hills               2   
221  New York City       Brooklyn          Ditmas Park               2   
141  New York City         Queens        East Elmhurst               2   
56   New York City       Brooklyn        East Flatbush               2   
72   New York City       Brooklyn        East New York               2   
2    New York City          Bronx          Eastchester               2   
45   New York City          Bronx             Edenwald               2   
176  New York City         Queens             Edgemere               2   
300  New York City       Brooklyn              Erasmus               2   
170  New York City         Queens         Far Rockaway               2   
3    New York City          Bronx            Fieldston               2   
75   New York City       Brooklyn            Flatlands               2   
181  New York City         Queens          Floral Park               2   
16   New York City          Bronx              Fordham               2   
158  New York City         Queens        Fresh Meadows               2   
144  New York City         Queens             Glendale               2   
202  New York City  Staten Island          Grymes Hill               2   
19   New York City          Bronx         High  Bridge               2   
295  New York City       Brooklyn        Highland Park               2   
182  New York City         Queens           Holliswood               2   
263  New York City         Queens        Jamaica Hills               2   
157  New York City         Queens    Kew Gardens Hills               2   
188  New York City         Queens            Laurelton               2   
187  New York City         Queens           Lindenwood               2   
23   New York City          Bronx             Longwood               2   
393       Portland      Southwest              MARKHAM               2   
83   New York City       Brooklyn          Marine Park               2   
20   New York City          Bronx              Melrose               2   
15   New York City          Bronx       Morris Heights               2   
25   New York City          Bronx           Morrisania               2   
21   New York City          Bronx           Mott Haven               2   
269  New York City          Bronx           Mount Eden               2   
270  New York City          Bronx           Mount Hope               2   
260  New York City       Brooklyn             New Lots               2   
195  New York City

In [77]:
#Cluster 4
neighborhoods_merged.loc[neighborhoods_merged['Cluster_Labels'] == 3, :]

City           Area          Neighborhood  Cluster_Labels  \
215  New York City  Staten Island              Annadale               3   
241  New York City  Staten Island         Arden Heights               3   
228  New York City  Staten Island              Arrochar               3   
152  New York City         Queens            Auburndale               3   
79   New York City       Brooklyn            Bath Beach               3   
175  New York City         Queens           Bay Terrace               3   
235  New York City  Staten Island           Bay Terrace               3   
13   New York City          Bronx          Bedford Park               3   
190  New York City         Queens          Belle Harbor               3   
156  New York City         Queens             Bellerose               3   
34   New York City          Bronx               Belmont               3   
47   New York City       Brooklyn           Bensonhurst               3   
80   New York City       Brooklyn          Borough Park               3   
297  New York City          Bronx             Bronxdale               3   
246  New York City  Staten Island            Bulls Head               3   
307       Portland           East            CENTENNIAL               3   
335       Portland      Northeast                 CULLY               3   
40   New York City          Bronx           Castle Hill               3   
208  New York City  Staten Island     Castleton Corners               3   
90   New York City       Brooklyn             City Line               3   
134  New York City         Queens                Corona               3   
55   New York City       Brooklyn         Crown Heights               3   
231  New York City  Staten Island          Dongan Hills               3   
154  New York City         Queens            Douglaston               3   
17   New York City          Bronx          East Tremont               3   
39   New York City          Bronx        Edgewater Park               3   
287  New York City  Staten Island           Egbertville               3   
214  New York City  Staten Island           Eltingville               3   
54   New York City       Brooklyn              Flatbush               3   
135  New York City         Queens          Forest Hills               3   
196  New York City         Queens  Forest Hills Gardens               3   
99   New York City       Brooklyn         Fort Hamilton               3   
337       Portland      Northeast            GRANT PARK               3   
94   New York City       Brooklyn            Georgetown               3   
155  New York City         Queens             Glen Oaks               3   
233  New York City  Staten Island            Grant City               3   
229  New York City  Staten Island              Grasmere               3   
50   New York City       Brooklyn             Gravesend               3   
213  New York City  Staten Island           Great Kills               3   
242  New York City  Staten Island            Greenridge               3   
309       Portland           East             HAZELWOOD               3   
310       Portland           East             HAZELWOOD               3   
103  New York City      Manhattan      Hamilton Heights               3   
243  New York City  Staten Island     Heartland Village               3   
289  New York City       Brooklyn             Homecrest               3   
133  New York City         Queens          Howard Beach               3   
236  New York City  Staten Island              Huguenot               3   
160  New York City         Queens        Jamaica Center               3   
136  New York City         Queens           Kew Gardens               3   
5    New York City          Bronx           Kingsbridge               3   
299  New York City          Bronx   Kingsbridge Heights               3   
153  New York City         Queens           Little Neck               3   
343       Portland      Northeast      

In [78]:
#Cluster 5
neighborhoods_merged.loc[neighborhoods_merged['Cluster_Labels'] == 4, :]

City           Area               Neighborhood  Cluster_Labels  \
320       Portland          North                ARBOR LODGE               4   
362       Portland      Southeast                  ARDENWALD               4   
306       Portland           East                      ARGAY               4   
352       Portland      Northwest          ARLINGTON HEIGHTS               4   
177  New York City         Queens                    Arverne               4   
129  New York City         Queens                    Astoria               4   
332       Portland      Northeast          BEAUMONT-WILSHIRE               4   
333       Portland      Northeast                      BOISE               4   
321       Portland          North                  BRIDGETON               4   
364       Portland      Southeast                   BROOKLYN               4   
365       Portland      Southeast                    BUCKMAN               4   
127  New York City      Manhattan          Battery Park City               4   
46   New York City       Brooklyn                  Bay Ridge               4   
151  New York City         Queens                    Bayside               4   
303  New York City         Queens                  Bayswater               4   
63   New York City       Brooklyn         Bedford Stuyvesant               4   
87   New York City       Brooklyn                Boerum Hill               4   
51   New York City       Brooklyn             Brighton Beach               4   
64   New York City       Brooklyn           Brooklyn Heights               4   
62   New York City       Brooklyn                   Bushwick               4   
322       Portland          North             CATHEDRAL PARK               4   
334       Portland      Northeast                  CONCORDIA               4   
366       Portland      Southeast         CRESTON-KENILWORTH               4   
386       Portland      Southwest                  CRESTWOOD               4   
247  New York City      Manhattan              Carnegie Hill               4   
66   New York City       Brooklyn            Carroll Gardens               4   
105  New York City      Manhattan             Central Harlem               4   
239  New York City  Staten Island                 Charleston               4   
116  New York City      Manhattan                    Chelsea               4   
244  New York City  Staten Island                    Chelsea               4   
100  New York City      Manhattan                  Chinatown               4   
12   New York City          Bronx                City Island               4   
249  New York City      Manhattan               Civic Center               4   
113  New York City      Manhattan                    Clinton               4   
84   New York City       Brooklyn               Clinton Hill               4   
65   New York City       Brooklyn                Cobble Hill               4   
254  New York City  Staten Island                    Concord               4   
78   New York City       Brooklyn               Coney Island               4   
29   New York City          Bronx               Country Club               4   
86   New York City       Brooklyn                   Downtown               4   
283  New York City       Brooklyn                      Dumbo               4   
81   New York City       Brooklyn              Dyker Heights               4   
367       Portland      Southeast               EASTMORELAND               4   
336       Portland      Northeast                      ELIOT               4   
106  New York City      Manhattan                East Harlem               4   
118  New York City      Manhattan               East Village               4   
95   New York City       Brooklyn          East Williamsburg               4   
132  New York City         Queens                   Elmhurst               4   
255  New York City  Staten Island               Emerson Hill               4   
387       Port

In [79]:
#Cluster 6
neighborhoods_merged.loc[neighborhoods_merged['Cluster_Labels'] == 5, :]

City           Area       Neighborhood  Cluster_Labels  \
323       Portland          North      EAST COLUMBIA               5   
388       Portland      Southwest           HAYHURST               5   
357       Portland      Northwest  NORTHWEST HEIGHTS               5   
315       Portland           East    PLEASANT VALLEY               5   
192  New York City         Queens         Somerville               5   
203  New York City  Staten Island          Todt Hill               5   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
323                  Park                   ATM        Nightlife Spot   
388                  Park                   ATM        Nightlife Spot   
357                  Park                   ATM        Nightlife Spot   
315                  Park                   ATM        Nightlife Spot   
192                  Park                   ATM        Nightlife Spot   
203                  Park                   ATM        Nightlife Spot   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
323             Pet Store           Pet Service              Pet Café   
388             Pet Store           Pet Service              Pet Café   
357             Pet Store           Pet Service              Pet Café   
315             Pet Store           Pet Service              Pet Café   
192             Pet Store           Pet Service              Pet Café   
203             Pet Store           Pet Service              Pet Café   

    7th Most Common Venue 8th Most Common Venue  9th Most Common Venue  \
323   Peruvian Restaurant    Persian Restaurant  Performing Arts Venue   
388   Peruvian Restaurant    Persian Restaurant  Performing Arts Venue   
357   Peruvian Restaurant    Persian Restaurant  Performing Arts Venue   
315   Peruvian Restaurant    Persian Restaurant  Performing Arts Venue   
192   Peruvian Restaurant    Persian Restaurant  Performing Arts Venue   
203   Peruvian Restaurant    Persian Restaurant  Performing Arts Venue   

    10th Most Common Venue  
323       Pedestrian Plaza  
388       Pedestrian Plaza  
357       Pedestrian Plaza  
315       Pedestrian Plaza  
192       Pedestrian Plaza  
203       Pedestrian Plaza

Create the dashboard

In [ ]:
# Create a dash application
app = JupyterDash(__name__)
#JupyterDash.infer_jupyter_proxy_config()

#Clear the layout and do not display exception till callback gets executed
#app.config.suppress_callback_exceptions = True

# Application layout
app.layout = html.Div(children=[html.H1('Comparable Neighborhoods: New York City - Portland OR',
                                        style={'textAlign':'center', 'color':'#503D36', 'font-size':24}),
                                
                                # Create an outer division 
                                html.Div([
                                    # Add an division
                                    html.Div([
                                        # Create an division for adding dropdown helper text for city
                                        html.Div(
                                            [
                                            html.H2('Destination City:', style={'margin-right': '2em'}),
                                            ]
                                        ),
                                        #Add city dropdown
                                        dcc.Dropdown(id='input-city',
                                                     options=[{'label':city, 'value':city} for city in cities],
                                                     placeholder="Select destination city",
                                                     style={'width':'80%', 'padding':'3px', 
                                                            'font-size':'20px', 'text-align-last':'center'}),
                        
                                    # Place them next to each other using the division style
                                    ], style={'display':'flex'}),
                                    
                                   # Add next division 
                                   html.Div([
                                       # Create an division for adding dropdown helper text for choosing neighborhood
                                        html.Div(
                                            [
                                            html.H2('Choose Neighborhood Where You Live:', style={'margin-right': '2em'})
                                            ]
                                        ),
                                        dcc.Dropdown(id='opt-neighborhoods', 
                                                     placeholder="Select neighborhood",
                                                     style={'width':'80%', 'padding':'3px', 'font-size': '20px', 'text-align-last' : 'center'}),
                                            # Place them next to each other using the division style
                                            ], style={'display': 'flex'}),  
                                          ]),
                                
                                html.Br(),
                                html.H2('Map of comparable neighborhoods', style={'margin-right': '2em'}),
                                
                                #add division for folio map
                                html.Div([ ], id='folio'),
                                
                                html.Br(),
                                html.H2('List of comparable neighborhoods and associated venue categories', style={'margin-right': '2em'}),
                                
                                #add division for neighborhood table
                                html.Div([
                                    dcc.dash_table.Datatable(
                                    id='neighborhood_table',
                                    columns=[{'name': i, 'id': i} for i in neighborhoods_merged.columns],)
                                ])])

#callback function for city drop down
@app.callback(dash.dependencies.Output('opt-neighborhoods', 'options'),
              dash.dependencies.Input('input-city', 'value'))

def update_neighborhood_dd(city):
    #check destination city value and return appropriate list of neighborhoods in the city where they live
    if city == 'New York City':
        return [{'label': i, 'value': i} for i in Portland_Neighborhoods]
        
    else:
        return [{'label': i, 'value': i} for i in NYC_Neighborhoods]
                
#callback function for neighborhood selection
@app.callback([dash.dependencies.Output('folio', 'children'),
              dash.dependencies.Output('neighborhood_table', 'children')],
              [dash.dependencies.Input('input_city', 'value'),
               dash.dependencies.Input('opt-neighborhoods', 'value')])

def get_neighborhood_info(selected_city, neighborhood):
    #check which city to set the general lat/long value for map
    if selected_city == 'New York City':
        latitude=NYC_latitude
        longitude=NYC_longitude
    else:
        latitude=Portland_latitude
        longitude=Portland_longitude
        
    #determine which cluster the neighborhood is in
    cluster=neighborhoods_merged.loc(neighborhood, 'Cluster_Labels')
    
    #now create a new dataframe with just that cluster
    target_df=neighborhoods_merged.query('Cluster_Labels==@cluster & City==@selected_city')
    
    #now create the folio map using the new dataframe
    map_neighborhoods = folium.Map(location=[latitude, longitude], zoom_start=11)
    
    # add markers to the map
    for lat, lon, poi in zip(target_df['Latitude'], target_df['Longitude'], target_df['Neighborhood']):
        label = folium.Popup(str(poi), parse_html=True)
        folium.CircleMarker(
            [lat, lon],
            radius=5,
            popup=label,
            fill=True,
            fill_opacity=0.7).add_to(map_neighborhoods)
    
    return [dcc.Graph(figure=map_neighborhoods),
            target_df.to_dict(orient='records')]

#if __name__ == '__main__':
app.run_server(mode="inline", host="localhost", debug=False)

    
    